# Resampling of Time Series
## Decimation
The Discrete Fourier Transform (DFT) can be used for some very basic signal processing operations. We can either use is for decimation, which results in redcution of the number of samples of a given time series or we can use it for interpolation, which is the opposite of decimation.
Decimation implies a reduction of time resolution and thus a decrease in the Nyquist frequency.
If the original signal contains higher frequency than the new Nyquist frequency
(after decimation) we get aliasing. Thus, a low pass filtering to the new Nyquist
frequency is required before decimation. Decimation and low-pass filtering can be
achieved in one step by using the DFT:
1. Transform the time series to the frequency domain using the DFT.
2. Reduce the Nyquist frequency by the desired factor (when using the Fast Fourier Transform, this should be a power of 2), and apply an appropriate taper. That’s the low-pass filter!
3. Do an inverse DFT of the modified spectrum with reduced Nyquist frequency and obtain a time series with greater sampling interval (because lower Nyquist frequency implies lower time resolution).

In [ ]:
# Import all required packages
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
from obspy import read
from scipy import signal

In [ ]:
# Read the data
st = read("../data/DOR50/*063")
print(st)

In [ ]:
def decimate(x, dt, factor):
    """
    Easy decimation for real input data x. Note, since new_dt might not be old_dt * 2**n,
    the decimation is not correct.
    x: Data array
    dt: sampling rate of x
    factor: factor for decimation, thus new sampling rate is dt/factor
    """
    # 1. Transform x to frequnecy domain
    ft = np.fft.rfft(x)
    freqs = np.fft.rfftfreq(n=len(x), d=dt)
    
    # 2. Get Nyquist Frequencies for both old dt an new dt
   
    
    # Find index of new Nyquist Frequnency in freqs
    index = np.where(freqs > new_f_ny)[0][0]
    
    # 3. Apply window function as lowpass filter and do inverse DFT 
    new_ft = ft[:index]
    new_ft = new_ft * signal.tukey(len(new_ft), alpha=0.25)
    x_new = np.fft.irfft(ft[:index])
    
    return x_new, dt*factor

In [ ]:
# Plot results for original and decimated data
# Read data from st
data = st[0].data[:100000]

# Apply Decimation
dec, dt_dec = decimate(data, dt=st[0].stats.delta, factor=2)

# Create arrays for time to plot
t_data = np.arange(0, len(data)) * st[0].stats.delta
t_dec = np.arange(0, len(dec)) * dt_dec

# Create plot widget
plt.plot(t_data, data - np.mean(data), alpha=0.5)
plt.plot(t_dec, dec - np.mean(dec), alpha=0.5)
plt.xlabel("Time (s)")
plt.ylabel("Amplitude (a.u.)")

## Interpolation
The opposite of decimation is interpolation. Here, we want a finer sampling of the
time series without changing the frequency content. We could do this in the time
domain by some interpolation rule using neighbouring samples. We can also do it
by using the DFT:
1. Transform the time series to the frequency domain using the DFT.
2. Append zeros to the spectrum thus increasing the Nyquist frequency.
3. Do an inverse DFT of the extended spectrum and obtain a time series with smaller sampling interval (because higher Nyquist frequency implies higher time resolution). The frequency content is unchanged!

In [ ]:
def interpolation(x, dt, new_dt):
    """
    Easy function for interpolation of a given data array to increase the the sampling rate.
    
    x: data array
    dt: sampling rate
    new_dt: new sampling rae
    """
    # 1. Transform x to frequnecy domain
    ft = np.fft.rfft(x)
    
    # Determine the number of zeros to add
    
    
    # 2. Append zeros to spectrum
    ft = np.concatenate((ft, np.zeros(append_zeros)))
    
    # 3. Do inverse DFT and determine new dt
    x_new = np.fft.irfft(ft)
    new_dt = t_max / len(x_new)
    
    return x_new, new_dt

In [ ]:
# Create plot
# Read data from st
data = st[0].data[:100000]

# Apply interpolation
interp, dt_interp = interpolation(data, dt=st[0].stats.delta, new_dt=1/150)

# Create time arrays
t_data = np.arange(0, len(data)) * st[0].stats.delta
t_interp = np.arange(0, len(interp)) * dt_interp

# Create plot widget
plt.plot(t_data, data - np.mean(data), alpha=0.5)
plt.plot(t_interp, interp - np.mean(interp), alpha=0.5)
plt.xlabel("Time (s)")
plt.ylabel("Amplitude (a.u.)")

## Comparison with function scipy.signal.resample
For documentation see https://docs.scipy.org/doc/scipy/reference/generated/scipy.signal.resample.html

In [ ]:
# Import funtion
from scipy.signal import resample

# Read data from st and create time array
data = st[0].data[:100000]
time = np.arange(0, len(data)) * st[0].stats.delta

# Apply resample funtion
resampled_x, resampled_t = resample(data, num=int(len(data)*2), t=time)

# Create plot
plt.plot(time, data - np.mean(data), alpha=0.5)
plt.plot(resampled_t, resampled_x - np.mean(resampled_x), alpha=0.5)
plt.xlabel("Time (s)")
plt.ylabel("Amplitude (a.u.)")